#####We will load data from silver to gold here for one of the sourcesystems and encourage the trainees to load the data for other source system.<br> 

In [0]:
#create schema for gold if it  does not exist
spark.sql("""CREATE SCHEMA IF NOT EXISTS psl_salesdev.gold MANAGED LOCATION 'abfss://sales@storageaccountname.dfs.core.windows.net/gold/'""")

DataFrame[]

___________________________________________________________________________________
#Load Dimensions

We will now creaate or dimension table structure if it already doesnt exist<br>
<b>this will be a managed [table](https://docs.databricks.com/en/tables/managed.html)

In [0]:
spark.sql("""
CREATE TABLE IF NOT EXISTS psl_salesdev.gold.tb_dim_product
( productKey STRING NOT NULL COMMENT 'Unique Key- Hashed value of the productID and source',
  productID STRING NOT NULL COMMENT 'Unique identifier for each product',
  productName STRING NOT NULL COMMENT 'Name of the product',
  subCategory STRING COMMENT 'Sub-category of the product',
  category STRING COMMENT 'Category of the product',
  source STRING COMMENT 'Source system of the data',
  createdAt TIMESTAMP COMMENT 'Timestamp when the data was ingested',
  updatedAt TIMESTAMP COMMENT 'Timestamp when the data was updated'
)
COMMENT 'This managed table contains product dimension data coming from different sources'
""")


DataFrame[]

######Let us read the product table data from the silver layer

In [0]:
df=spark.table("psl_salesdev.silver.product_cleaned")

We will now create the key column for our table

In [0]:
from pyspark.sql.functions import sha1,current_timestamp,col,concat_ws
#Lets first create the key column with combination without hashing
df=df.withColumn("productKey",concat_ws("|",col("productID"),col("source"))) 
#concat_ws is used to join the columns with a specific delimiter in this case | for example productID|source

#Now lets hash the key column
source_df=df.withColumn("productKey",sha1(col("productKey"))).dropDuplicates('productKey')
source_df.limit(5).display()

productID productName subCategory category source ingestionTimestamp productKey FUR-CH-10003312 Hon 2090 “Pillow Soft” Series Mid Back Swivel/Tilt Chairs Chairs Furniture Retail CSV 2024-09-09T19:36:52.229Z 001a593a4c5ddad23e24fd41821a7da13ddd8aeb TEC-PH-10000169 ARKON Windshield Dashboard Air Vent Car Mount Holder Phones Technology Retail CSV 2024-09-09T19:36:52.229Z 00518a64a08232452dcb86711d24d55777adfc62 FUR-BO-10002202 Atlantic Metals Mobile 2-Shelf Bookcases, Custom Colors Bookcases Furniture Retail CSV 2024-09-09T19:36:52.229Z 005b3778efbb1e664732df68e9ad8980aa98144e FUR-FU-10001940 Staple-based wall hangings Furnishings Furniture Retail CSV 2024-09-09T19:36:52.229Z 006eac7fbcdacffa05392b4976fc38d77cf5e2c2 OFF-BI-10001679 GBC Instant Index System for Binding Systems Binders Office Supplies Retail CSV 2024-09-09T19:36:52.229Z 00a8b42510cccb85e440fa019e2be314199de766

###SCD1 script

In [0]:
from delta.tables import DeltaTable


# Load the target table using catalog.schema.table 
target_table = DeltaTable.forName(spark, "psl_salesdev.gold.tb_dim_product")

# Perform the merge with conditional update
target_table.alias("target").merge(
    source_df.alias("source"),
    "target.productKey = source.productKey"  # Business key for the merge
).whenMatchedUpdate(
    condition = (
        (col("source.productName") != col("target.productName")) |
        (col("source.subCategory") != col("target.subCategory"))
    ),
    set = {
        "productName": "source.productName",
        "subCategory": "source.subCategory",
        "updatedAt": current_timestamp()  # Update `updated_date` if fields differ
    }
).whenNotMatchedInsert(
    values = {
        "productKey": "source.productKey",
        "productID": "source.productID",
        "productName": "source.productName",
        "subCategory": "source.subCategory",
        "category": "source.category",
        "source": "source.source",
        "createdAt": current_timestamp(),  # Set `created_date` on insert
    }
).execute()


Let us verify if our dimension write was succesful

In [0]:
%sql
select * from psl_salesdev.gold.tb_dim_product

productKey productID productName subCategory category source createdAt updatedAt 3a684f159a43d668d23c73913bd2c0db8c916b1b TEC-PH-10000486 Plantronics HL10 Handset Lifter Phones Technology Retail CSV 2024-09-10T04:32:08.281Z null 409cff111f556613a58d3f40d9e3ec8b80b2c91d TEC-AC-10003832 Logitech P710e Mobile Speakerphone Accessories Technology Retail CSV 2024-09-10T04:32:08.281Z null 8f1c9eaee5668b9eb13253537bdd999480bfb7a4 TEC-AC-10002076 Microsoft Natural Keyboard Elite Accessories Technology Retail CSV 2024-09-10T04:32:08.281Z null 3f04dfa1a4777875cba280bf42bfdfe839f9f99d TEC-PH-10004667 Cisco 8x8 Inc. 6753i IP Business Phone System Phones Technology Retail CSV 2024-09-10T04:32:08.281Z null b03ff9c908164b7fa3e4aff42590519b85b4b542 OFF-BI-10000545 GBC Ibimaster 500 Manual ProClick Binding System Binders Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 0301d35acb2a3e5410e6a1a74767acfb59aa9679 OFF-PA-10003543 Xerox 1985 Paper Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 585278f7f8828b399f4897d75505b108e2fed148 OFF-PA-10000994 Xerox 1915 Paper Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 56c250b5ae5c636c70577f6372241d32f314ab49 FUR-TA-10003008 Lesro Round Back Collection Coffee Table, End Table Tables Furniture Retail CSV 2024-09-10T04:32:08.281Z null 2974a20b89e1dbc874d0a4030c7d0cd0eaa255ea OFF-PA-10002464 HP Office Recycled Paper (20Lb. and 87 Bright) Paper Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null d7848474f1c147f7ecc107fbc3abcdebe29b6245 TEC-AC-10001109 Logitech Trackman Marble Mouse Accessories Technology Retail CSV 2024-09-10T04:32:08.281Z null 478e6edf7fba55b330ad8d0be56134147e708ac1 FUR-FU-10004904 "Eldon ""L"" Workstation Diamond Chairmat" Furnishings Furniture Retail CSV 2024-09-10T04:32:08.281Z null d4f1b726aba591f83ad45dec86ea246024b33e1b OFF-PA-10000246 Riverleaf Stik-Withit Designer Note Cubes Paper Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 9604a235133e8f7defa7e1e12a126a486ec5765d OFF-LA-10003388 Avery 5 Labels Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 27a393d9d23d307cfc1f82890470d0ba1b70a619 TEC-MA-10003673 Hewlett-Packard Desktjet 6988DT Refurbished Printer Machines Technology Retail CSV 2024-09-10T04:32:08.281Z null 1869418c4514638984f4c381e6350f3535b0c709 OFF-BI-10001890 Avery Poly Binder Pockets Binders Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 3e902061dd66466a5d36e28c54bb15714a908905 OFF-BI-10000136 Avery Non-Stick Heavy Duty View Round Locking Ring Binders Binders Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 94740bd0f49780d08cfb30ad21f0d1e59d469d12 TEC-AC-10002018 AmazonBasics 3-Button USB Wired Mouse Accessories Technology Retail CSV 2024-09-10T04:32:08.281Z null 41f398b0b5c14b0b3d7adab6fd12658e34f73fd1 TEC-MA-10000423 Texas Instruments TI-34 Scientific Calculator Machines Technology Retail CSV 2024-09-10T04:32:08.281Z null 3e49d98e3e0d2584a176b320148609299370a79d OFF-SU-10004290 "Acme Design Line 8"" Stainless Steel Bent Scissors w/Champagne Handles Supplies Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 1af94b384a0efd5edf56972c292211a415348978 OFF-PA-10002479 Xerox 4200 Series MultiUse Premium Copy Paper (20Lb. and 84 Bright) Paper Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 74d50b470db7d571d401507bdef17f476a1e3b4d OFF-ST-10004180 Safco Commercial Shelving Storage Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null 0f2566da00de01e634f3ecb134a75be3110adc70 FUR-FU-10001861 Floodlight Indoor Halogen Bulbs, 1 Bulb per Pack, 60 Watts Furnishings Furniture Retail CSV 2024-09-10T04:32:08.281Z null f0883d9357b91ed4de64f67cc20276f5f53f7337 FUR-TA-10002041 Bevis Round Conference Table Top, X-Base Tables Furniture Retail CSV 2024-09-10T04:32:08.281Z null a32759103af10b9e54729b3589e1e3fd5b596bb4 OFF-AR-10004974 Newell 342 Art Office Supplies Retail CSV 2024-09-10T04:32:08.281Z null a06db9874fd042fb97b5a6d28684615c0c5c5277 OFF-BI-10001294 Fellowes Binding Cases Binders Office Supplies Retai

__________________________________________________________________________
#Load Facts

In [0]:
#First we will create the structure of our fact table
spark.sql("""
CREATE TABLE IF NOT EXISTS psl_salesdev.gold.tb_fact_sales
( productKey STRING NOT NULL COMMENT 'Unique Key- Hashed value of the productID and source',
  orderDate DATE COMMENT 'Date of the order',
  salesValue DOUBLE COMMENT 'Sales Value of the product',
  totatOrders INT COMMENT 'Total number of orders',
  quantity INT COMMENT 'Quantity of the product',
  profit DOUBLE COMMENT 'Profit of the product',
  source    STRING COMMENT 'Source of the data',
  createdAt TIMESTAMP COMMENT 'Timestamp when the data was ingested'
)
COMMENT 'This managed table contains product sales data coming from different sources'
""")

DataFrame[]

####Read data from the silver table

In [0]:
df_sales_silver=spark.table("psl_salesdev.silver.sales_cleaned")

create productkey and aggregate the data based on productKey and date level

In [0]:
from pyspark.sql.functions import concat_ws,sha1
df_sales_silver_withkey=df_sales_silver.withColumn('ProductKey',concat_ws("|",df_sales_silver.productId,df_sales_silver.source))
df_sales_silver_withkey_withkey=df_sales_silver_withkey.withColumn('ProductKey',sha1(df_sales_silver_withkey.ProductKey))

After Key creation, let us now aggregate the df

In [0]:
from pyspark.sql.functions import *

In [0]:
df_agg=df_sales_silver_withkey_withkey.groupBy('ProductKey','orderDate','source')\
    .agg(sum('quantity').cast('int').alias('quantity'),
         sum('sales').alias('salesValue'),
         countDistinct('orderId').cast('int').alias('totatOrders'),
         sum('profit').alias('profit')
         )\
             .withColumn('createdAt',current_timestamp())\
                 .select(
                    'productKey' ,
                    'orderDate' ,
                    'salesValue',
                    'totatOrders' ,
                    'quantity' ,
                    'profit' ,
                    'source'  ,
                    'createdAt'
                    )

In [0]:
df_agg.limit(5).display()

productKey orderDate salesValue totatOrders quantity profit source createdAt f09a9c1cd9a9bff199e4de17bca75f93435fd5a4 2016-05-21 111.96 1 2 54.8604 Retail CSV 2024-09-12T14:37:14.336Z d38f55198a15e5d9dd5ad2d51e689511ebb1b134 2017-12-28 10.36 2 4 1.628 Retail CSV 2024-09-12T14:37:14.336Z b0f5aa9a5d163f8733035934144627a88b648f3e 2017-12-08 27.15 1 5 13.3035 Retail CSV 2024-09-12T14:37:14.336Z 409cff111f556613a58d3f40d9e3ec8b80b2c91d 2017-07-11 1287.45 1 5 244.6155 Retail CSV 2024-09-12T14:37:14.336Z 1f8b776065e1e78f6ffcbf20886ccc5d1d9b85cc 2017-05-14 64.4 1 5 1.932 Retail CSV 2024-09-12T14:37:14.336Z

save the data to sales table

In [0]:
df_agg.write.mode('append').saveAsTable('psl_salesdev.gold.tb_fact_sales')

Let us now verify if the data has been written to our sales table

In [0]:
%sql
select * from psl_salesdev.gold.tb_fact_sales

productKey orderDate salesValue totatOrders quantity profit source createdAt f09a9c1cd9a9bff199e4de17bca75f93435fd5a4 2016-05-21 111.96 1 2 54.8604 Retail CSV 2024-09-10T08:13:26.81Z d38f55198a15e5d9dd5ad2d51e689511ebb1b134 2017-12-28 10.36 2 4 1.628 Retail CSV 2024-09-10T08:13:26.81Z b0f5aa9a5d163f8733035934144627a88b648f3e 2017-12-08 27.15 1 5 13.3035 Retail CSV 2024-09-10T08:13:26.81Z 409cff111f556613a58d3f40d9e3ec8b80b2c91d 2017-07-11 1287.45 1 5 244.6155 Retail CSV 2024-09-10T08:13:26.81Z 1f8b776065e1e78f6ffcbf20886ccc5d1d9b85cc 2017-05-14 64.4 1 5 1.932 Retail CSV 2024-09-10T08:13:26.81Z e0dec97a288ae365a1f335298cd431aa4e6d2778 2016-09-02 22.911 1 7 -17.5651 Retail CSV 2024-09-10T08:13:26.81Z 5fc8aa2d07d9fcc2b084d6c3f73c2c27f0419eba 2016-12-18 18.84 1 3 6.0288 Retail CSV 2024-09-10T08:13:26.81Z 81b666a39ac5df97c5ee6e11de6463e68fe6a0a3 2014-09-19 7.16 1 2 3.58 Retail CSV 2024-09-10T08:13:26.81Z 7273da8a8500d58003866a64b984d99be79e34bc 2014-04-07 122.97 1 3 60.2553 Retail CSV 2024-09-10T08:13:26.81Z 7951d981138d8623926dbe2cd89a6f6b4c228c74 2017-12-08 113.568 1 2 -18.4548 Retail CSV 2024-09-10T08:13:26.81Z bb878f8a51eb017b6d77925dad04250d3638e5dd 2015-09-10 106.68 1 6 33.0708 Retail CSV 2024-09-10T08:13:26.81Z 5438a65640c908e7862b06b18bedd53fbfe839d8 2017-12-24 null 1 37 0.0 Retail CSV 2024-09-10T08:13:26.81Z d3be4b29f4e596d05b7011a50b329505fc153d0b 2016-03-13 552.56 1 5 -138.14 Retail CSV 2024-09-10T08:13:26.81Z d8c6578867675e09d15e78e4f85a21d64aecfa6f 2016-06-26 135.95 1 1 39.4255 Retail CSV 2024-09-10T08:13:26.81Z 3e8274ac92f77132f8e6b2b611de1868b3f7f4bf 2016-06-12 226.56 1 6 63.4368 Retail CSV 2024-09-10T08:13:26.81Z bca5c24ce0ff0ca3741d77421f577bf24db7a2f5 2017-11-04 194.352 1 3 -43.7292 Retail CSV 2024-09-10T08:13:26.81Z 7352cd6d78d0d180661879436b11f546b6e5f8ea 2015-09-12 12.6 1 4 6.048 Retail CSV 2024-09-10T08:13:26.81Z 6f0e0a8cba24808a9d48bbc7c590d92d6b453dcc 2014-12-08 45.68 1 2 21.0128 Retail CSV 2024-09-10T08:13:26.81Z 6445848caaa69834b99ec00db0baeb2bb5731860 2016-06-17 40.74 1 3 0.4074 Retail CSV 2024-09-10T08:13:26.81Z e845bfc358716a08934eda065b18884f8c7880cc 2017-08-07 51.75 1 1 15.525 Retail CSV 2024-09-10T08:13:26.81Z 46bc56149e6c72ed890e08e5e9c1677619ec998d 2017-09-07 73.008 1 9 26.4654 Retail CSV 2024-09-10T08:13:26.81Z 324ee327abd57fd220bfbb1b94a6ce6945e79139 2016-05-14 31.104 1 6 10.8864 Retail CSV 2024-09-10T08:13:26.81Z 44289e60a6492871731b3e02bf25dea0552ce456 2016-06-18 6.848 1 2 2.14 Retail CSV 2024-09-10T08:13:26.81Z 2fc68754c8757167285ceb2e42fec50a53b36f5a 2015-01-02 89.584 1 2 4.4792 Retail CSV 2024-09-10T08:13:26.81Z 991ca57e2e90f8e82f71848091961dd4ef68496e 2014-08-24 12.672 1 3 4.4352 Retail CSV 2024-09-10T08:13:26.81Z 909d5cff1cd2b94fcd0f2632b2ea1e0bbc4eb5ce 2015-11-12 223.888 1 7 69.965 Retail CSV 2024-09-10T08:13:26.81Z d24f38259fb252ffbb9671191dc6e01bd7f0e4f2 2017-05-13 530.34 1 2 95.4612 Retail CSV 2024-09-10T08:13:26.81Z fb2ccf6809cc3c0e33d817d16a9a76009a7bd511 2015-11-12 5.238 1 2 -4.0158 Retail CSV 2024-09-10T08:13:26.81Z c0ab75c3e3c4eb9cd1550c37a8f49ca4263bb472 2014-09-01 31.104 1 6 10.8864 Retail CSV 2024-09-10T08:13:26.81Z b1d4bc403b141a2fc358e78314cf43e4e7fe4e72 2014-11-30 102.24 1 4 -16.614 Retail CSV 2024-09-10T08:13:26.81Z c257291cb128c4715de9ef0f2b7f7119c32227e7 2016-10-15 29.46 1 6 14.4354 Retail CSV 2024-09-10T08:13:26.81Z 1b1e3e5010994a8df79d0f2c7885a45ed2e978b4 2017-09-20 13.76 1 2 6.3296 Retail CSV 2024-09-10T08:13:26.81Z d712b957f96a9b830e2710f9e5ee7cb13722db78 2016-04-14 81.2 1 5 12.18 Retail CSV 2024-09-10T08:13:26.81Z 60ee73ce7345318eb6540ee11136440bb87d316c 2017-04-10 7.61 1 1 3.5767 Retail CSV 2024-09-10T08:13:26.81Z 8681a29e94da490e1760d3e295c2ecb3f418ed23 2014-03-11 32.96 1 2 14.1728 Retail CSV 2024-09-10T08:13:26.81Z 722f26f592e33209dfd57197d737c6ba3bfc7c22 2017-09-04 43.176 1 3 15.1116 Retail CSV 2024-09-10T08:13:26.81Z 97e17352687834bf0fc32e8f019aeee5401901dd 2014-11-01 15.696 1 3 5.1012 Retail CSV 2024-09-10T08:13:26.81Z 31c16089f8b61ccf2792734d0caf6d63542e55b6 2